In [ ]:
using Plots;
Plots.plotly();

In [26]:
function plot_birth_death_process(b, d, N)
    # create the matrix D
    D = zeros(N+1, N+1);
    D[1,1] = 1;
    for i = 2:N
        D[i, i-1] = d[i];
        D[i, i] = - b[i] - d[i];
        D[i, i+1] = b[i];
    end
    D[N+1, N] = d[N+1];
    D[N+1, N+1] = -d[N+1];
    # create the vector c
    c = ones(N+1);
    c *= -1;
    c[1] = 0;
    # calculate the expected extinction time
    τ = D^(-1)*c;
    # plot result
    x = collect(0:N);
    Plots.plot(x,τ)
end


plot_birth_death_process (generic function with 1 method)

In [28]:
br = 0.025;
dr = 0.025;
N = 20;
b = collect(0:N)*br
d = collect(0:N)*dr
Plots.plot(collect(0:20), [b,d, b+d])

In [29]:
plot_birth_death_process(b, d, N)

In [31]:
r = 0.015;
K = 10;
N = 20;
b = [r*(i - i^2/(2*K)) for i = 0:2*K];
d = [r*i^2/(2*K) for i = 0:2*K];
Plots.plot(collect(0:20), [b,d, b+d])

In [32]:
plot_birth_death_process(b, d, N)

In [33]:
r = 0.015;
K = 10;
N = 20;
b = [r*i for i = 0:N-1];
append!(b, 0)
d = [r*i^2/K for i = 0:N];
Plots.plot(collect(0:20), [b,d, b+d])

In [34]:
plot_birth_death_process(b, d, N)

In [110]:
function plot_dist(b, d, N, rep, X)
    for i = 2:rep
        for j = 0:N
            X[i,j+1] += X[i-1, j+1]*(1-d[j+1]-b[j+1])
            (j > 1) && (X[i,j+1] += X[i-1,j]*b[j])
            (j < N) && (X[i,j+1] += X[i-1,j+2]*d[j+2])
        end
    end
    Plots.surface(collect(0:N), collect(1:rep), X)
end

plot_dist (generic function with 3 methods)

In [111]:
r = 0.015;
K = 10;
N = 20;
rep = 1000;
X = zeros(rep, N+1);
X[1,2] = 1; 
b = [r*(i - i^2/(2*K)) for i = 0:2*K];
d = [r*i^2/(2*K) for i = 0:2*K];
plot_dist(b,d,N,rep)

In [112]:
r = 0.015;
K = 10;
N = 20;
rep = 1000;
X = zeros(rep, N+1);
X[1,2] = 1; 
b = [r*i for i = 0:N-1];
append!(b, 0)
d = [r*i^2/K for i = 0:N];
plot_dist(b,d,N, rep)

In [114]:
r = 0.004;
K = 50;
N = 100;
rep = 2000;
X = zeros(rep, N+1);
X[1,6] = 1;
b = [r*(i - i^2/(2*K)) for i = 0:2*K];
d = [r*i^2/(2*K) for i = 0:2*K];
plot_dist(b,d,N,rep)

In [126]:
function plot_comp(b, d, N, rep, X, K, r, x0)
    for i = 2:rep
        for j = 0:N
            X[i,j+1] += X[i-1, j+1]*(1-d[j+1]-b[j+1])
            (j > 1) && (X[i,j+1] += X[i-1,j]*b[j])
            (j < N) && (X[i,j+1] += X[i-1,j+2]*d[j+2])
        end
    end
    f(x) = 5*K*exp(r*x) / (5*exp(r*x) + K - 5);
    y = [f(x) for x = 1:rep];
    Plots.plot(collect(1:rep), [X*collect(0:N), y]);
end

plot_comp (generic function with 1 method)

In [127]:
r = 0.004;
K = 50;
N = 100;
rep = 2000;
X = zeros(rep, N+1);
X[1,6] = 1;
x0 = 5;
b = [r*(i - i^2/(2*K)) for i = 0:2*K];
d = [r*i^2/(2*K) for i = 0:2*K];
plot_comp(b, d, N, rep, X, K, r, x0)

In [86]:
function get_quasistationary(b,d,N)
    # create the matrix D
    D = zeros(N, N);
    for i = 1:N
        (i > 1) && (D[i, i-1] = b[i-1]);
        D[i, i] = 1 - b[i] - d[i];
        (i < N) && (D[i, i+1] = d[i+1]);
    end
    # calculate the eigenvectors
    (W, V) = eig(D);
    ind = [abs(W[i] - 1) < 1e-9 for i = 1:N];
    y = V[:, ind];
    y /= sum(y);
    return(y);
end

get_quasistationary (generic function with 1 method)

In [130]:
r = 0.004;
K = 50;
N = 100;
b = [r*(i - i^2/(2*K)) for i = 1:2*K];
d = [r*i^2/(2*K) for i = 1:2*K];
d[1] = 0;
q = get_quasistationary(b,d,N)
print("Mean: ", real(sum(collect(1:N).*q)))

Mean: 49.48957397081342

In [133]:
Plots.plot(collect(1:N), real(q))

In [101]:
r = 0.015;
K = 10;
N = 20;
b = [r*(i - i^2/(2*K)) for i = 1:2*K];
d = [r*i^2/(2*K) for i = 1:2*K];
d[1] = 0;
q = get_quasistationary(b,d,N)
print("Mean: ", sum(collect(1:20).*q))

Mean: 9.434825819217039

In [89]:
Plots.plot(collect(1:N), q)

In [102]:
r = 0.015;
K = 10;
N = 20;
b = [r*i for i = 1:N-1];
append!(b, 0)
d = [r*i^2/K for i = 1:N];
d[1] = 0;
q = get_quasistationary(b,d,N)
print("Mean: ", sum(collect(1:N).*q))

Mean: 8.83955285038186

In [103]:
Plots.plot(collect(1:N), q)